### Background:  Pivot Bio runs an extensive field demonstration program to introduce farmers to our products, covering thousands of acres across the United States. Ideally, we would have an agronomist visit every farmer to address issues, but as we include more and more farmers it becomes harder and harder to visit. We have established a UAV imagery process that allows for monitoring and quality control of smaller trials, but we need a UAV based process to monitor our on-farm and commercial trials. Ideally, the system would inform Agronomists when an issue is detected, so they can contact the grower.   

### Goal: Development of a model using satellite/UAV remote sensing datasets from free repositories to detect product failure with > 60% accuracy by the V6 crop growth stage 

# Collect data from S3

In [1]:
import ftl.dw_call as dw
import boto3
from copy import deepcopy
from pathlib import Path
import os
import shutil
import glob

import pandas as pd
from pandas.errors import ParserError
import numpy as np
from datetime import datetime
from fiona.collection import DriverError
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import seaborn as sns

import geopandas as gpd
from osgeo import gdal
from shapely.ops import unary_union
from shapely.geometry import Polygon
from io import BytesIO
import rasterio
import rasterio as rio
import rasterio.plot
from rasterio.transform import Affine
from rasterstats import zonal_stats
import pyproj

from affine import Affine
from rasterio.mask import mask
from shapely.geometry import Polygon,Point
from shapely import wkt
from shapely.geometry import box

import warnings
warnings.filterwarnings("ignore")

In [2]:
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import confusion_matrix

from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import make_scorer
from sklearn.pipeline import Pipeline

from sklearn.linear_model import LogisticRegression

from sklearn import metrics
from sklearn.metrics import average_precision_score
from sklearn.metrics import roc_auc_score, roc_curve, precision_score, recall_score, f1_score, precision_recall_curve, accuracy_score

In [4]:
### work on protocol '22-ZEAMX-US502'
keys = ['22-ZEAMX-US502']

### Download & Calculation: access sataellite data (plots and image) from S3; calculate 

In [12]:
s3 = boto3.resource('s3')
bucket = s3.Bucket('pivot-uav-collab')

non_raw = []
for kw in keys:
    print(f"Accessing Keyword: {kw}")
    objects = bucket.objects.filter(
        Prefix=f'planet/{kw}',
        MaxKeys=40000
    )

    non_raw.extend([x for x in objects if '_RAW' not in x.key.upper()])
rasters = {
    x.key: x.bucket_name for x in non_raw 
    if any(s in x.key.upper() for s in ['_MULTISPECTRAL.',])
}

plots = {
    x.key: x.bucket_name for x in non_raw 
    if 'GPKG' in x.key.upper()
}

Accessing Keyword: 22-ZEAMX-US502


In [13]:
print(len(plots))
plots

23


{'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA02-5ERB/22-ZEAMX-US502-IA02-5ERB_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA03-5TIARK/22-ZEAMX-US502-IA03-5TIARK_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA04-5BLOMG/22-ZEAMX-US502-IA04-5BLOMG_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA05-5SHOOK/22-ZEAMX-US502-IA05-5SHOOK_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA06-5STORB/22-ZEAMX-US502-IA06-5STORB_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IL01-5DENTO/22-ZEAMX-US502-IL01-5DENTO_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IL02-5BRODI/22-ZEAMX-US502-IL02-5BRODI_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IL03-5WADE/22-ZEAMX-US502-IL03-5WADE_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IL04-5LAUX/22-ZEAMX-US502-IL04-5LAUX_plots.gpkg': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IL06-5JONES/22-ZEAMX-US5

In [14]:
print(len(rasters))
rasters

1328


{'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220527_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220601_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220603_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220607_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220617_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220619_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US502-IA01-5HEIMS_20220620_ANALYTIC8B_MULTISPECTRAL.tif': 'pivot-uav-collab',
 'planet/22-ZEAM

In [15]:
def read_s3_contents(bucket_name, key):
    response = s3.Object(bucket_name, key).get()
    return response['Body'].read()

def calc_nd(band1, band2):
    return((band1 - band2) / (band1 + band2))

def multipolygon_to_polygon(geometry):
    if geometry.geom_type.lower() == 'multipolygon':
        return geometry.geoms[0]
    else:
        return geometry

In [16]:
# https://developers.planet.com/docs/apis/data/sensors/
# Band	Name	Wavelength (fwhm)	Interoperable with Sentinel-2
# 1	Coastal Blue	443 (20)	Yes - with Sentinel-2 band 1
# 2	Blue	490 (50)	Yes - with Sentinel-2 band 2
# 3	Green I	531 (36)	No equivalent with Sentinel-2
# 4	Green	565 (36)	Yes - with Sentinel-2 band 3
# 5	Yellow	610 (20)	No equivalent with Sentinel-2
# 6	Red	665 (31)	Yes - with Sentinel-2 band 4
# 7	Red Edge	705 (15)	Yes - with Sentinel-2 band 5
# 8	NIR	865 (40)	Yes - with Sentinel-2 band 8a

# select index:  RED:5  RED EDGE:6   NIR:7

In [17]:
%%time
full = []
failed = {}
for image, bucket in rasters.items():
    # get image metadata
    trial, file = image.split(r'/')[-2:]
    date = file.split(r'_')[1]
    
    # search for matching plots on trial name
    try:
        plot = [x for x in plots.keys() if trial in x][0]
    except IndexError:
        failed.update({image:'no plot (indexerror)'})
        continue
    
    # read in plots and buffer 1m inwards
    try:
        gpkg = gpd.read_file(BytesIO(read_s3_contents(bucket, plot)))
        gpkg = gpkg.dropna(axis='columns', how='all')
    except DriverError:
        failed.update({plot:'plot issue (drivererror)'})
        continue
    if not set([
        'trial_id', 'plot', 'row', 'col', 'treatment', 'geometry'
    ]).issubset(set(gpkg.columns)):
        failed.update({plot:'plot metadata issue (missing column)'})
        continue
    if gpkg.crs.axis_info[0].unit_name != 'metre':
        gpkg = gpkg.to_crs('epsg:5070')
    gpkg['geometry'] = gpkg['geometry'].apply(multipolygon_to_polygon)
    gpkg['geometry'] = gpkg.buffer(-1)
    
    # read in image
    with rio.open(BytesIO(read_s3_contents(bucket, image))) as src:
        data = src.read()
        profile = src.profile
    
    # set plot crs to image crs
    if not profile['crs'] == gpkg.crs:
        gpkg = gpkg.to_crs(profile['crs'])

    # band math
    vis = {}
    vis['ndvi'] = calc_nd(data[7], data[5])
    vis['ndre'] = calc_nd(data[7], data[6])
    try:
        ndvi = pd.DataFrame(zonal_stats(
            gpkg,
            vis['ndvi'],
            affine=profile['transform'],
            stats=['mean', 'std']
        ))
    except AttributeError:
        failed.update({image:'zonal stats issue (attributeerror)'})
        continue
    ndvi = ndvi.rename(columns={x: f'ndvi_{x}' for x in ndvi.columns})
    ndre = pd.DataFrame(zonal_stats(
        gpkg,
        vis['ndre'],
        affine=profile['transform'],
        stats=['mean', 'std']
    ))
    ndre = ndre.rename(columns={x:f'ndre_{x}' for x in ndre.columns})
    
    gpkg['flight_date'] = date
    gpkg['filename'] = plot
    gpkg['flightname'] = file
    try:
        gpkg['flight_date'] = pd.to_datetime(gpkg['flight_date'])
    except:
        pass
    out = pd.concat([gpkg, ndvi, ndre], axis=1)
    full.append(out)


Wall time: 31min 31s


In [18]:
failed

{}

In [19]:
full

[    Shape_Leng  plot        Protocol                    trial_id  col  row  \
 0   622.973321   404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1   
 1   622.021053   103  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    9    1   
 2   621.885045   402  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    8    1   
 3   622.836889   403  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   15    1   
 4   622.700983   304  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   14    1   
 5   621.612834   302  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    6    1   
 6   621.476729   301  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    5    1   
 7   621.340521   202  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    4    1   
 8   620.931704   101  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    1    1   
 9   621.204317   201  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    3    1   
 10  622.429371   204  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   12    1   
 11  621.749140   401  22-ZEAMX-US502  22-ZEAMX-US50

In [20]:
df = pd.concat(full)
df['protocol__name'] = df['trial_id'].str.rsplit('-', 2).str[0]
# there's an issue with a file flight date
# df.loc[df['flight_date']=='08172022', 'flight_date'] = '20220817'
df['flight_date'] = pd.to_datetime(df['flight_date'])
df.groupby(['protocol__name', 'trial_id']).agg({'flight_date':'nunique'})

flight_date
protocol__name trial_id                               
22-ZEAMX-US502 22-ZEAMX-US502-IA01-5HEIMS           55
               22-ZEAMX-US502-IA02-5ERB             28
               22-ZEAMX-US502-IA03-5TIARK           26
               22-ZEAMX-US502-IA04-5BLOMG           49
               22-ZEAMX-US502-IA05-5SHOOK           56
               22-ZEAMX-US502-IA06-5STORB           53
               22-ZEAMX-US502-IL01-5DENTO           58
               22-ZEAMX-US502-IL02-5BRODI           69
               22-ZEAMX-US502-IL03-5WADE            58
               22-ZEAMX-US502-IL04-5LAUX            73
               22-ZEAMX-US502-IL06-5JONES           43
               22-ZEAMX-US502-IN03-5GOHN            56
               22-ZEAMX-US502-MI01-5HOWE            60
               22-ZEAMX-US502-MN01-5JOHNS           59
               22-ZEAMX-US502-MN02-5BACKM           46
               22-ZEAMX-US502-MO01-5JOHNS           62
               22-ZEAMX-US502-NE01-5RHODE           70
               22-ZEAMX-US502-NE02-5WALGR           81
               22-ZEAMX-US502-OH02-5COX             41
               22-ZEAMX-US502-OK01-5ISAAC           90
               22-ZEAMX-US502-SD01-5WIESE           66
               22-ZEAMX-US502-TN01-5ADAMS           51
               22-ZEAMX-US502-WI01-5COWAN           78

In [21]:
df.groupby(['protocol__name']).agg({'trial_id':'nunique'})

trial_id
protocol__name          
22-ZEAMX-US502        23

In [25]:
print(df.columns)
df.head(1)

Index(['Shape_Leng', 'plot', 'Protocol', 'trial_id', 'col', 'row', 'PB_Trt',
       'Fert_trt', 'Shape_Le_1', 'treatment', 'geometry', 'flight_date',
       'filename', 'flightname', 'ndvi_mean', 'ndvi_std', 'ndre_mean',
       'ndre_std', 'Protocol_1', 'Name', 'protocol__name'],
      dtype='object')


Shape_Leng plot        Protocol                    trial_id  col  row  \
0  622.973321  404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1   

  PB_Trt Fert_trt  Shape_Le_1  treatment  ... flight_date  \
0    NTC   N:100%  608.341399          3  ...  2022-05-23   

                                            filename  \
0  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   

                                          flightname ndvi_mean  ndvi_std  \
0  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...  0.215124  0.009255   

   ndre_mean  ndre_std  Protocol_1 Name  protocol__name  
0   0.165431  0.009924         NaN  NaN  22-ZEAMX-US502  

[1 rows x 21 columns]

In [27]:
# df.to_csv('Planet502_info.csv',index=False)

In [62]:
df_new=df.iloc[:,1:18]

In [63]:
df_new.head(2)

plot        Protocol                    trial_id  col  row PB_Trt Fert_trt  \
0  404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1    NTC   N:100%   
1  103  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    9    1    NTC   N:100%   

   Shape_Le_1  treatment                                           geometry  \
0  608.341399          3  POLYGON ((-91.47935 42.62288, -91.47936 42.622...   
1  607.389133          3  POLYGON ((-91.47987 42.62288, -91.47988 42.622...   

  flight_date                                           filename  \
0  2022-05-23  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   
1  2022-05-23  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   

                                          flightname  ndvi_mean  ndvi_std  \
0  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...   0.215124  0.009255   
1  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...   0.201352  0.011940   

   ndre_mean  ndre_std  
0   0.165431  0.009924  
1   0.159553  0.010224

###  Match the growth stage

In [38]:
### read stage data
data = pd.read_csv('22-ZEAMX-US502 metadata and growthstage date estimates.csv')
data.head(2)

trial_id  Unnamed: 0                  trial_id.1  \
0  22-ZEAMX-US502-IA01-5HEIMS           0  22-ZEAMX-US502-IA01-5HEIMS   
1  22-ZEAMX-US502-IA05-5SHOOK           1  22-ZEAMX-US502-IA05-5SHOOK   

                               gps_center planting_date harvest_date qc_score  \
0   42.67675452094237, -91.44210007041691     5/15/2022    11/2/2022   Yellow   
1  42.114235199729805, -96.22117929160596     5/18/2022   11/18/2022    Green   

  experiment_name  year        protocol  ...        V11        V12         VT  \
0       FTR001184  2022  22-ZEAMX-US502  ...  7/11/2022  7/22/2022  7/29/2022   
1       FTR001188  2022  22-ZEAMX-US502  ...   7/5/2022  7/15/2022  7/20/2022   

          R1         R2         R3         R4         R5         R6  \
0  8/25/2022   9/3/2022  9/13/2022  9/26/2022  11/3/2022        NaN   
1  8/10/2022  8/18/2022  8/27/2022   9/4/2022  9/20/2022  9/23/2022   

          R6+  
0         NaN  
1  11/19/2022  

[2 rows x 33 columns]

In [54]:
filtered_data= data.iloc[:,[0]+[6]+list(range(11,33))]

### transfer the string to datetime
stage=filtered_data.iloc[:,2:24].applymap(lambda x: datetime.strptime(x, "%m/%d/%Y").date() if not pd.isna(x) else x)
stage['trial_id']=filtered_data['trial_id']
stage['qc_score']=filtered_data['qc_score']

In [64]:
trials=df_new['trial_id'].tolist()
dates=df_new['flight_date'].tolist()
growth_stages=[]

for i in range(len(trials)):
    ### get trail_id and image date
    trial_id = str(trials[i])
    date_string = str(dates[i]).split()[0]
    date_format = "%Y-%m-%d"
    
    ### match the exact trail
    select=stage[stage['trial_id'] == trial_id]
    
    ### match the date and save
    growth_stage=select.iloc[0,0:-2].sub(datetime.strptime(date_string, date_format).date()).abs().idxmin()
    growth_stages.append(growth_stage)

In [65]:
df_new['stage']=growth_stages

In [66]:
df_new['stage'].unique()

array(['V0', 'VE', 'V1', 'V3', 'V4', 'V5', 'V6', 'V7', 'V9', 'V10', 'V11',
       'V12', 'VT', 'R1', 'R2', 'R3', 'R4', 'R5', 'V2', 'V8', 'R6', 'R6+'],
      dtype=object)

In [67]:
df_new.head(2)

plot        Protocol                    trial_id  col  row PB_Trt Fert_trt  \
0  404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1    NTC   N:100%   
1  103  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS    9    1    NTC   N:100%   

   Shape_Le_1  treatment                                           geometry  \
0  608.341399          3  POLYGON ((-91.47935 42.62288, -91.47936 42.622...   
1  607.389133          3  POLYGON ((-91.47987 42.62288, -91.47988 42.622...   

  flight_date                                           filename  \
0  2022-05-23  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   
1  2022-05-23  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   

                                          flightname  ndvi_mean  ndvi_std  \
0  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...   0.215124  0.009255   
1  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...   0.201352  0.011940   

   ndre_mean  ndre_std stage  
0   0.165431  0.009924    V0  
1   0.159553  0.010224    V0

### Get the yield data

In [58]:
all_yield = pd.read_csv('biomass_measurements__yield_bu_acre_502.csv')
all_yield.head(3)

protocol__name        experiment__trial_id  plot__lookup_key  \
0  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS             101.0   
1  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS             102.0   
2  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS             103.0   

                 experiment__gps_center       value  
0  42.67675452094237,-91.44210007041691  249.963684  
1  42.67675452094237,-91.44210007041691  258.665060  
2  42.67675452094237,-91.44210007041691  255.604752

In [72]:
### extract the yield column and GPS center of the plot
all_yield.columns=['Protocol','trial_id','plot','GPS_center','yield']
all_yield.head(3)

Protocol                    trial_id   plot  \
0  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS  101.0   
1  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS  102.0   
2  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS  103.0   

                             GPS_center       yield  
0  42.67675452094237,-91.44210007041691  249.963684  
1  42.67675452094237,-91.44210007041691  258.665060  
2  42.67675452094237,-91.44210007041691  255.604752

In [75]:
df_merge3=pd.merge(df_new,all_yield.iloc[:,1:5],on=['trial_id','plot'])
# df_merge3.to_csv('merged502_data.csv',index=False)
df_merge3.head(2)

plot        Protocol                    trial_id  col  row PB_Trt Fert_trt  \
0  404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1    NTC   N:100%   
1  404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1    NTC   N:100%   

   Shape_Le_1  treatment                                           geometry  \
0  608.341399          3  POLYGON ((-91.47935 42.62288, -91.47936 42.622...   
1  608.341399          3  POLYGON ((-91.47935 42.62288, -91.47936 42.622...   

  flight_date                                           filename  \
0  2022-05-23  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   
1  2022-05-27  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   

                                          flightname  ndvi_mean  ndvi_std  \
0  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...   0.215124  0.009255   
1  22-ZEAMX-US502-IA01-5HEIMS_20220527_ANALYTIC8B...   0.251247  0.006969   

   ndre_mean  ndre_std stage                            GPS_center       yield  
0   0.165431  0.009924    V0  42.67675452094237,-91.44210007041691  260.873976  
1   0.190193  0.011378    V0  42.67675452094237,-91.44210007041691  260.873976

In [76]:
df_merge3[['treatment', 'Fert_trt', 'PB_Trt']].value_counts().sort_index()

treatment  Fert_trt      PB_Trt     
1          N:100%-40 LB  NTC            3747
2          N:100%-40 LB  2022-PV40ST    3747
3          N:100%        NTC            4025
4          N:100%        2022-PV40ST    4025
5          N:0 LB        NTC             505
6          N:0 LB        2022-PV40ST     505
dtype: int64

### Drop NaN values

In [21]:
df_load=pd.read_csv('merged502_data.csv')
df_merge3=df_load.copy()

In [22]:
print(df_merge3.columns)

df_merge3.head(1)

Index(['plot', 'Protocol', 'trial_id', 'col', 'row', 'PB_Trt', 'Fert_trt',
       'Shape_Le_1', 'treatment', 'geometry', 'flight_date', 'filename',
       'flightname', 'ndvi_mean', 'ndvi_std', 'ndre_mean', 'ndre_std', 'stage',
       'GPS_center', 'yield'],
      dtype='object')


plot        Protocol                    trial_id  col  row PB_Trt Fert_trt  \
0   404  22-ZEAMX-US502  22-ZEAMX-US502-IA01-5HEIMS   16    1    NTC   N:100%   

   Shape_Le_1  treatment                                           geometry  \
0  608.341399          3  POLYGON ((-91.47935421237469 42.62287547098129...   

  flight_date                                           filename  \
0  2022-05-23  planet/22-ZEAMX-US502-IA01-5HEIMS/22-ZEAMX-US5...   

                                          flightname  ndvi_mean  ndvi_std  \
0  22-ZEAMX-US502-IA01-5HEIMS_20220523_ANALYTIC8B...   0.215124  0.009255   

   ndre_mean  ndre_std stage                            GPS_center       yield  
0   0.165431  0.009924    V0  42.67675452094237,-91.44210007041691  260.873976

In [23]:
df_all=df_merge3[['plot','trial_id','treatment','geometry','flight_date','GPS_center','ndvi_mean', 'ndvi_std', 'ndre_mean', 'ndre_std','stage',
       'yield']]

In [45]:
df_all.head(1)

plot                    trial_id  treatment  \
0   404  22-ZEAMX-US502-IA01-5HEIMS          3   

                                            geometry flight_date  \
0  POLYGON ((-91.47935421237469 42.62287547098129...  2022-05-23   

                             GPS_center  ndvi_mean  ndvi_std  ndre_mean  \
0  42.67675452094237,-91.44210007041691   0.215124  0.009255   0.165431   

   ndre_std stage       yield  
0  0.009924    V0  260.873976

In [24]:
### use when load as a string not geometric, as the wkt.loads() function from the wkt module (presumably imported as wkt) to parse a WKT geometry string and convert it into a corresponding geometric object
# df_all['geometry']=df_all['geometry'].apply(lambda x: wkt.loads(x) if x else None)
print(df_all.shape)

(16554, 12)


In [25]:
df_merge3[df_merge3.ndvi_mean.notnull()].shape 

(13285, 20)

In [26]:
df_all.isnull().sum()

plot              0
trial_id          0
treatment         0
geometry          0
flight_date       0
GPS_center        0
ndvi_mean      3269
ndvi_std       3269
ndre_mean      3269
ndre_std       3269
stage             0
yield             0
dtype: int64

In [27]:
print(df_all[df_all.ndvi_mean.isnull()].shape)
images_with_nan_list=df_all[df_all.ndvi_mean.isnull()]
images_with_nan_list.to_csv('images_with_nan_list_502.csv',index=None)

(3269, 12)


In [13]:
df_all[df_all['ndvi_mean'].isnull()].trial_id.unique()

array(['22-ZEAMX-US502-IA03-5TIARK', '22-ZEAMX-US502-IA06-5STORB',
       '22-ZEAMX-US502-MI01-5HOWE', '22-ZEAMX-US502-MN01-5JOHNS',
       '22-ZEAMX-US502-OK01-5ISAAC'], dtype=object)

In [28]:
df_all = df_all.dropna()

In [29]:
df_all.isnull().sum()

plot           0
trial_id       0
treatment      0
geometry       0
flight_date    0
GPS_center     0
ndvi_mean      0
ndvi_std       0
ndre_mean      0
ndre_std       0
stage          0
yield          0
dtype: int64

In [30]:
df_all.shape

(13285, 12)

In [31]:
df_yield=df_all.copy()
df_yield=df_yield.groupby(['trial_id','treatment']).agg({'yield':'mean'})
df_yield=df_yield.reset_index()

In [90]:
df_yield.groupby(['trial_id']).agg({'treatment':'nunique'})

treatment
trial_id                             
22-ZEAMX-US502-IA01-5HEIMS          4
22-ZEAMX-US502-IA02-5ERB            4
22-ZEAMX-US502-IA04-5BLOMG          6
22-ZEAMX-US502-IA05-5SHOOK          6
22-ZEAMX-US502-IL01-5DENTO          4
22-ZEAMX-US502-IL02-5BRODI          4
22-ZEAMX-US502-IL03-5WADE           6
22-ZEAMX-US502-IL04-5LAUX           4
22-ZEAMX-US502-IN03-5GOHN           6
22-ZEAMX-US502-MI01-5HOWE           6
22-ZEAMX-US502-MO01-5JOHNS          6
22-ZEAMX-US502-NE02-5WALGR          2
22-ZEAMX-US502-OH02-5COX            6
22-ZEAMX-US502-TN01-5ADAMS          6

In [33]:
ids_with_treat_3 = df_yield[df_yield['treatment'] == 3]['trial_id']
ids_without_treat_3 = df_yield[~df_yield['trial_id'].isin(ids_with_treat_3)]['trial_id']

print(ids_without_treat_3)

df_yield[df_yield['trial_id'].isin(ids_with_treat_3)]

8     22-ZEAMX-US502-IA03-5TIARK
9     22-ZEAMX-US502-IA03-5TIARK
10    22-ZEAMX-US502-IA03-5TIARK
23    22-ZEAMX-US502-IA06-5STORB
24    22-ZEAMX-US502-IA06-5STORB
25    22-ZEAMX-US502-IA06-5STORB
56    22-ZEAMX-US502-MN02-5BACKM
57    22-ZEAMX-US502-MN02-5BACKM
58    22-ZEAMX-US502-MN02-5BACKM
59    22-ZEAMX-US502-MN02-5BACKM
74    22-ZEAMX-US502-OK01-5ISAAC
Name: trial_id, dtype: object


trial_id  treatment       yield
0   22-ZEAMX-US502-IA01-5HEIMS          1  262.289473
1   22-ZEAMX-US502-IA01-5HEIMS          2  265.105004
2   22-ZEAMX-US502-IA01-5HEIMS          3  261.421157
3   22-ZEAMX-US502-IA01-5HEIMS          4  254.066227
4     22-ZEAMX-US502-IA02-5ERB          1  235.805276
..                         ...        ...         ...
76  22-ZEAMX-US502-TN01-5ADAMS          2  196.677855
77  22-ZEAMX-US502-TN01-5ADAMS          3  207.651960
78  22-ZEAMX-US502-TN01-5ADAMS          4  209.110405
79  22-ZEAMX-US502-TN01-5ADAMS          5  140.676236
80  22-ZEAMX-US502-TN01-5ADAMS          6  136.297558

[70 rows x 3 columns]

In [34]:
to_plot=df_yield[df_yield['trial_id'].isin(ids_with_treat_3)]

In [46]:
df_yield[df_yield['trial_id']=='22-ZEAMX-US502-MN02-5BACKM']

trial_id  treatment       yield
64  22-ZEAMX-US502-MN02-5BACKM          1  217.463361
65  22-ZEAMX-US502-MN02-5BACKM          2  213.194346
66  22-ZEAMX-US502-MN02-5BACKM          5  140.653011
67  22-ZEAMX-US502-MN02-5BACKM          6  160.337769

In [35]:
# Create a mapping dictionary to replace the values
value_map = {
    1: 3,
    2: 7,
    3: 1,
    4: 8,
    5: 9,
    6: 10
}

to_plot['treatment'] = to_plot['treatment'].replace(value_map)

In [38]:
count_df.to_csv('502_treatment.csv',index=False)

In [37]:
count_df

treatment  Identify  Percentage
0          1         0    0.000000
1          3         4   14.285714
2          7         5   17.857143
3          8         3   10.714286
4          9         8   28.571429
5         10         8   28.571429

In [2]:
to_plot.groupby(['treatment'])['Identify'].count()

##we would plot the bar figure from 501 and 502 together, not here individually 

### Get the boundary

In [7]:
df_all.head(1)

plot                    trial_id  treatment  \
0   404  22-ZEAMX-US502-IA01-5HEIMS          3   

                                            geometry flight_date  \
0  POLYGON ((-91.47935421237469 42.62287547098129...  2022-05-23   

                             GPS_center  ndvi_mean  ndvi_std  ndre_mean  \
0  42.67675452094237,-91.44210007041691   0.215124  0.009255   0.165431   

   ndre_std stage       yield  
0  0.009924    V0  260.873976

In [8]:
ids_with_treat_3 = df_all[df_all['treatment'] == 3]['trial_id'].unique()

df_all=df_all[df_all['trial_id'].isin(ids_with_treat_3)]

In [9]:
df_all['geometry']=df_all['geometry'].apply(lambda x: wkt.loads(x) if x else None)

print(df_all.shape)

(12198, 12)


#### stage V3

In [68]:
df_v3=df_all[df_all.stage=='V3']

### Get the boundary of each trial to cut the downloaed HyP3 tiff files
######################################################################

tmp=df_v3.groupby(['trial_id']).agg({'geometry': unary_union})
tmp=tmp.reset_index()

# Extract boundaries for each polygon in trial
tmp['upper_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[3])
tmp['lower_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[1])
tmp['left_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[0])
tmp['right_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[2])

# get a rectangle boundary for later extraction of the SAR image
tmp['outline']=tmp.apply(lambda row: Polygon([(row['left_boundary'], row['lower_boundary']),
                                               (row['right_boundary'], row['lower_boundary']),
                                               (row['right_boundary'], row['upper_boundary']),
                                               (row['left_boundary'], row['upper_boundary'])]),
                           axis=1)
                         
### save a file to 
tmp[['trial_id','left_boundary', 'right_boundary','lower_boundary','upper_boundary']].to_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\boundarys_V3.csv',header=None,index=None)

### save all shp files
output_folder = r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\all_shps\stageV3'

# Convert the drao a GeoDataFrame

gdf1 = gpd.GeoDataFrame(tmp, geometry='outline')

# Iterate over each row in the GeoDataFrame
for index, row in gdf1.iterrows():
    id_value = row['trial_id']
    outline_geom = row['outline']
    
    # Create a new GeoDataFrame for the current polygon
    poly_gdf = gpd.GeoDataFrame({'geometry': [outline_geom]}, crs=gdf1.crs)
    
    # Save the polygon to a shapefile using the ID as the filename
    output_filename = os.path.join(output_folder, f'{id_value}.shp')
    poly_gdf.to_file(output_filename)

#### stage V4

In [69]:
df_v4=df_all[df_all.stage=='V4']

### Get the boundary of each trial to cut the downloaed HyP3 tiff files
######################################################################

tmp=df_v4.groupby(['trial_id']).agg({'geometry': unary_union})
tmp=tmp.reset_index()

# Extract boundaries for each polygon in trial
tmp['upper_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[3])
tmp['lower_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[1])
tmp['left_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[0])
tmp['right_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[2])

# get a rectangle boundary for later extraction of the SAR image
tmp['outline']=tmp.apply(lambda row: Polygon([(row['left_boundary'], row['lower_boundary']),
                                               (row['right_boundary'], row['lower_boundary']),
                                               (row['right_boundary'], row['upper_boundary']),
                                               (row['left_boundary'], row['upper_boundary'])]),
                           axis=1)
                         
### save a file to 
tmp[['trial_id','left_boundary', 'right_boundary','lower_boundary','upper_boundary']].to_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\boundarys_V4.csv',header=None,index=None)

### save all shp files
output_folder = r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\all_shps\stageV4'

# Convert the drao a GeoDataFrame

gdf1 = gpd.GeoDataFrame(tmp, geometry='outline')

# Iterate over each row in the GeoDataFrame
for index, row in gdf1.iterrows():
    id_value = row['trial_id']
    outline_geom = row['outline']
    
    # Create a new GeoDataFrame for the current polygon
    poly_gdf = gpd.GeoDataFrame({'geometry': [outline_geom]}, crs=gdf1.crs)
    
    # Save the polygon to a shapefile using the ID as the filename
    output_filename = os.path.join(output_folder, f'{id_value}.shp')
    poly_gdf.to_file(output_filename)

#### stage V6

In [70]:
df_v6=df_all[df_all.stage=='V6']

### Get the boundary of each trial to cut the downloaed HyP3 tiff files
######################################################################

tmp=df_v6.groupby(['trial_id']).agg({'geometry': unary_union})
tmp=tmp.reset_index()

# Extract boundaries for each polygon in trial
tmp['upper_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[3])
tmp['lower_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[1])
tmp['left_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[0])
tmp['right_boundary'] = tmp['geometry'].apply(lambda mp: mp.bounds[2])

# get a rectangle boundary for later extraction of the SAR image
tmp['outline']=tmp.apply(lambda row: Polygon([(row['left_boundary'], row['lower_boundary']),
                                               (row['right_boundary'], row['lower_boundary']),
                                               (row['right_boundary'], row['upper_boundary']),
                                               (row['left_boundary'], row['upper_boundary'])]),
                           axis=1)
                         
### save a file to 
tmp[['trial_id','left_boundary', 'right_boundary','lower_boundary','upper_boundary']].to_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\boundarys_V6.csv',header=None,index=None)

### save all shp files
output_folder = r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\all_shps\stageV6'

# Convert the drao a GeoDataFrame

gdf1 = gpd.GeoDataFrame(tmp, geometry='outline')

# Iterate over each row in the GeoDataFrame
for index, row in gdf1.iterrows():
    id_value = row['trial_id']
    outline_geom = row['outline']
    
    # Create a new GeoDataFrame for the current polygon
    poly_gdf = gpd.GeoDataFrame({'geometry': [outline_geom]}, crs=gdf1.crs)
    
    # Save the polygon to a shapefile using the ID as the filename
    output_filename = os.path.join(output_folder, f'{id_value}.shp')
    poly_gdf.to_file(output_filename)

### Define to extract amplitude and precipitation

In [11]:
### load the downloaded weather station data
weather=pd.read_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\weather\station_weather.csv')

In [12]:
# Convert the flight date column to datetime
df_all['flight_date'] = pd.to_datetime(df_all['flight_date']).dt.date
weather['DATE'] = pd.to_datetime(weather['DATE']).dt.date

### Define to extract amplitude and precipitation

In [13]:
def find_closest_point_to_centroid(polygon_geom, points_df):
    # Extract the polygon geometry from the DataFrame
#     polygon_geom = polygon_df['geometry'].iloc[0]

    # Calculate the centroid of the polygon
    centroid = polygon_geom.centroid

    closest_point = None
    min_distance = float('inf')

    # Iterate through the DataFrame of points
    for _, point in points_df.iterrows():
        point_lat = point['LATITUDE']
        point_lon = point['LONGITUDE']
        rain_value = point['PRCP']

        # Create a Shapely Point object from the latitude and longitude
        point_geom = Point(point_lon, point_lat)

        # Calculate the distance between the point and the centroid
        distance = centroid.distance(point_geom)

        # Update the closest point and rain value if a closer point is found
        if distance < min_distance:
            min_distance = distance
            closest_point = point
            closest_point['PRCP'] = rain_value

    return closest_point

In [14]:
def extract_statistics(image_path, polygon):
    stats = zonal_stats(polygon, image_path, stats=['mean', 'median', 'std'])
    mean_value = stats[0]['mean']
    median_value = stats[0]['median']
    std_value = stats[0]['std']
    return mean_value, median_value, std_value

In [15]:
def cal_rolling_sums(station,given_date,window_size):
    df_select=weather[weather.STATION==station]
    df_select=df_select.sort_values('DATE')
    df_select.set_index('DATE', inplace=True)
    rolling_sum = df_select['PRCP'].rolling(window=window_size, min_periods=window_size).sum().loc[given_date]
    return rolling_sum

# Feature Engineering

## StageV3

#### Get amplitude

In [29]:
####### RESAMPLE THE IMAGE TO FINER RESOLUTION
################################################################################################################

# ### folder to store the cut images
input_path = r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\cut_tif\stage3"

#### folder to store the resample images
output_path= r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\resample_tif\stage31"

for file in os.listdir(input_path):
    
    file_path=os.path.join(input_path,file)

    src = rasterio.open(file_path)

    # Calculate the new dimensions and resolution
    new_resolution = (0.00001, -0.00001)  # New resolution in meters
    new_width = src.width * src.transform.a / new_resolution[0]
    new_height = src.height * src.transform.e / new_resolution[1]

    # Create the output TIFF file with the new dimensions and resolution
    
#     output_file = r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\cut_tif2\output.tif"

    
    prefix=file.split(".")[0]
    output_file = os.path.join(output_path, f"{prefix}_resample.tif")
    
    
    dst_transform = Affine(new_resolution[0], 0, src.transform.c, 0, new_resolution[1], src.transform.f)
    dst_profile = src.profile
    dst_profile.update(transform=dst_transform, width=int(new_width), height=int(new_height))

    # Perform the resampling
    with rasterio.open(output_file, 'w', **dst_profile) as dst:
        for i in range(1, src.count + 1):
            rasterio.warp.reproject(
                source=rasterio.band(src, i),
                destination=rasterio.band(dst, i),
                src_transform=src.transform,
                src_crs=src.crs,
                dst_transform=dst_transform,
                dst_crs=src.crs,  # Assuming the same CRS
                resampling=rasterio.enums.Resampling.bilinear
            )

In [19]:
df_v3=df_all[df_all.stage=='V3']

In [30]:
input_tif_folder= r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\resample_tif\stage31"
cnt=0

######
for index, row in df_v3.iterrows():
    cnt+=1
    print(cnt)
    id_value = row['trial_id']
    image_path_VH = os.path.join(input_tif_folder,f'{id_value}_VH_resample.tif')
    image_path_VV = os.path.join(input_tif_folder,f'{id_value}_VV_resample.tif')

    # Check if the TIF image exists
    if os.path.exists(image_path_VH) and os.path.exists(image_path_VV):
        # Extract the polygon from the 'geometry' column
        polygon = row['geometry']

        # Extract the statistics from the image within the polygon
        mean_vh, median_vh, std_vh = extract_statistics(image_path_VH, polygon)
        mean_vv, median_vv, std_vv = extract_statistics(image_path_VH, polygon)

        # Update the dataframe with the statistics
        df_v3.at[index, 'mean_vh'] = mean_vh
        df_v3.at[index, 'median_vh'] = median_vh
        df_v3.at[index, 'std_vh'] = std_vh
        df_v3.at[index, 'mean_vv'] = mean_vv
        df_v3.at[index, 'median_vv'] = median_vv
        df_v3.at[index, 'std_vv'] = std_vv
    else:
        # TIF image doesn't exist, set the values as NaN
        df_v3.at[index, 'mean_vh'] = np.nan
        df_v3.at[index, 'median_vh'] = np.nan
        df_v3.at[index, 'std_vh'] = np.nan
        df_v3.at[index, 'mean_vv'] = np.nan
        df_v3.at[index, 'median_vv'] = np.nan
        df_v3.at[index, 'std_vv'] = np.nan

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209


#### Get weather

In [32]:
df_v3.head(1)

plot                    trial_id  treatment  \
5   404  22-ZEAMX-US502-IA01-5HEIMS          3   

                                            geometry flight_date  \
5  POLYGON ((-91.47935421237469 42.62287547098129...  2022-06-17   

                             GPS_center  ndvi_mean  ndvi_std  ndre_mean  \
5  42.67675452094237,-91.44210007041691   0.388062  0.011177   0.305768   

   ndre_std stage       yield    mean_vh  median_vh    std_vh    mean_vv  \
5   0.00788    V3  260.873976 -23.804274 -23.315357  2.036357 -23.804274   

   median_vv    std_vv  
5 -23.315357  2.036357

In [50]:
# Convert the flight date column to datetime
df_v3['flight_date'] = pd.to_datetime(df_v3['flight_date']).dt.date
weather['DATE'] = pd.to_datetime(weather['DATE']).dt.date

In [34]:
cnt=0

for index, row in df_v3.iterrows():
    cnt+=1
    print(cnt)
    # Extract ID, geometry, and flight date from the current row
    ID = row['trial_id']
    geometry = row['geometry']
    flight_date = row['flight_date']
#     print(flight_date)

    # Filter the weather archive dataframe based on the flight date
    filtered_weather_df = weather[weather['DATE'] == flight_date]
    
    # Find the point closest to the centroid of the polygon
    if not filtered_weather_df.empty:
        closest_point = find_closest_point_to_centroid(geometry, filtered_weather_df)

        # Retrieve the rain and elevation values for the closest weather station
        closest_station_rain = closest_point['PRCP']
        closest_station_rain_5d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],5)
        closest_station_rain_10d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],10)
        closest_station_rain_15d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],15)
#         closest_station_elevation = closest_point['ELEVATION']

        # Add the rain and elevation values as new columns in the original dataframe
        df_v3.at[index, 'closest_station_rain'] = closest_station_rain
        df_v3.at[index, 'closest_station_rain_5d'] = closest_station_rain_5d
        df_v3.at[index, 'closest_station_rain_10d'] = closest_station_rain_10d
        df_v3.at[index, 'closest_station_rain_15d'] = closest_station_rain_15d
#         df_v3.at[index, 'closest_station_elevation'] = closest_station_elevation
    else:
#         print(index,ID,flight_date)
        df_v3.at[index, 'closest_station_rain'] = np.nan
        df_v3.at[index, 'closest_station_rain_5d'] = np.nan
        df_v3.at[index, 'closest_station_rain_10d'] = np.nan
        df_v3.at[index, 'closest_station_rain_15d'] = np.nan
#         df_v3.at[index, 'closest_station_elevation'] = np.nan

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209


In [36]:
df_v3_get=df_v3.groupby(['trial_id','treatment']).agg({'ndvi_mean':'mean','ndvi_std':'mean','ndre_mean':'mean','ndre_std':'mean','yield':'mean',
                                             'mean_vh':'mean','median_vh':'mean', 'std_vh':'mean', 'mean_vv':'mean', 'median_vv':'mean', 'std_vv':'mean',
                                             'closest_station_rain':'mean','closest_station_rain_5d':'mean','closest_station_rain_10d':'mean',
                                             'closest_station_rain_15d':'mean',
                                             'geometry': unary_union})
df_v3_get=df_v3_get.reset_index()

#### Add latitude and longitude as features

In [37]:
get_centroid=df_v3_get[['geometry']]
gdf = gpd.GeoDataFrame(get_centroid, geometry='geometry')
# Compute the centroid of each polygon
gdf['centroid'] = gdf['geometry'].centroid

# Extract latitude and longitude from the centroid
df_v3_get['latitude']=gdf.centroid.y
df_v3_get['longitude'] = gdf.centroid.x

df_v3_get['longitude']=df_v3_get['longitude']+360

#### NDRE and NDVI

In [38]:
scaler = MinMaxScaler()

df_v3_get['norm_ndvi_mean'] = scaler.fit_transform(df_v3_get[['ndvi_mean']])
df_v3_get['norm_ndvi_std'] = scaler.fit_transform(df_v3_get[['ndvi_std']].values)
df_v3_get['norm_ndre_mean'] = scaler.fit_transform(df_v3_get[['ndre_mean']].values)
df_v3_get['norm_ndre_std'] = scaler.fit_transform(df_v3_get[['ndre_std']].values)

#### treatment

In [39]:
treat_encoder = OneHotEncoder(handle_unknown='ignore')
treat_onehot=treat_encoder.fit_transform(df_v3_get[['treatment']])
treatments=pd.DataFrame(treat_onehot.toarray())

all_treatments=treat_encoder.categories_[0]
for i in range(len(all_treatments)):
    df_v3_get[str(all_treatments[i])]=treatments.iloc[:,i]

### Judge product failure based on yield data
trials=df_v3_get['trial_id'].tolist()
yields=df_v3_get['yield'].tolist()

Identifys=[]

for i in range(len(trials)):
    trail_id=trials[i]
    yie=float(yields[i])
    
    select=df_v3_get[(df_v3_get['trial_id'] == trail_id) & (df_v3_get['treatment']==3)]
    
#     print(trail_id)
    reference = select['yield'].values[0]
    
    check = 1 if abs(yie-reference) > reference*0.03 else 0
    Identifys.append(check)
    
df_v3_get['Identify'] = Identifys

#### Get more features - compare with treatment 1 condition

In [40]:
df_v3_get['ndvi_mean__diff'] = df_v3_get.groupby('trial_id')['norm_ndvi_mean'].transform(lambda x: x - x.iloc[0])
df_v3_get['ndvi_std_diff'] = df_v3_get.groupby('trial_id')['norm_ndvi_std'].transform(lambda x: x - x.iloc[0])
df_v3_get['ndre_mean_diff'] = df_v3_get.groupby('trial_id')['norm_ndre_mean'].transform(lambda x: x - x.iloc[0])
df_v3_get['ndre_std_diff'] = df_v3_get.groupby('trial_id')['norm_ndre_std'].transform(lambda x: x - x.iloc[0])

In [41]:
df_v3_get['mean_amp']=(df_v3_get['mean_vh']+df_v3_get['mean_vv'])/2
df_v3_get['std_amp']=(df_v3_get['std_vh']+df_v3_get['std_vv'])/2

df_v3_get['mean_vh_diff'] = df_v3_get.groupby('trial_id')['mean_vh'].transform(lambda x: x - x.iloc[0])
df_v3_get['median_vh_diff'] = df_v3_get.groupby('trial_id')['median_vh'].transform(lambda x: x - x.iloc[0])
df_v3_get['std_vh_diff'] = df_v3_get.groupby('trial_id')['std_vh'].transform(lambda x: x - x.iloc[0])
df_v3_get['mean_vv_diff'] = df_v3_get.groupby('trial_id')['mean_vv'].transform(lambda x: x - x.iloc[0])
df_v3_get['median_vv_diff'] = df_v3_get.groupby('trial_id')['median_vv'].transform(lambda x: x - x.iloc[0])
df_v3_get['std_vv_diff'] = df_v3_get.groupby('trial_id')['std_vv'].transform(lambda x: x - x.iloc[0])

In [70]:
df_v3_get.head(1)

trial_id  treatment  ndvi_mean  ndvi_std  ndre_mean  \
0  22-ZEAMX-US502-IA01-5HEIMS          1   0.383388  0.010286    0.30543   

   ndre_std       yield    mean_vh  median_vh    std_vh  ...  ndre_mean_diff  \
0  0.012132  262.289473 -20.057127 -20.063561  1.805224  ...             0.0   

   ndre_std_diff   mean_amp   std_amp  mean_vh_diff  median_vh_diff  \
0            0.0 -20.057127  1.805224           0.0             0.0   

   std_vh_diff mean_vv_diff  median_vv_diff  std_vv_diff  
0          0.0          0.0             0.0          0.0  

[1 rows x 43 columns]

In [71]:
df_v3_get.columns=['trial_id', 'treatment', 'ndvi_mean', 'ndvi_std', 'ndre_mean',
       'ndre_std', 'yield', 'mean_vh', 'median_vh', 'std_vh', 'mean_vv',
       'median_vv', 'std_vv', 'closest_station_rain',
       'closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d', 'geometry', 'latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       '7','8','1','9','10','11','Identify', 'ndvi_mean__diff',
       'ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff', 'mean_amp',
       'std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff',
       'mean_vv_diff', 'median_vv_diff', 'std_vv_diff']

In [15]:
# ### save all data in case
df_v3_get.to_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\df_v3_get_incase_502.csv',index=None)

In [14]:
df_v3_get=pd.read_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\df_v3_get_incase_502.csv')

### update identify method
trials=df_v3_get['trial_id'].tolist()
yields=df_v3_get['yield'].tolist()

Identifys2=[]

for i in range(len(trials)):
    trail_id=trials[i]
    yie=float(yields[i])
    
    select=df_v3_get[(df_v3_get['trial_id'] == trail_id) & (df_v3_get['treatment']==3)]
    
#     print(trail_id)
    reference = select['yield'].values[0]
    
    check = 1 if yie - reference < (reference * -0.03) else 0
    Identifys2.append(check)
    
df_v3_get['Identify2'] = Identifys2

In [11]:
df_v3_get.columns

Index(['trial_id', 'treatment', 'ndvi_mean', 'ndvi_std', 'ndre_mean',
       'ndre_std', 'yield', 'mean_vh', 'median_vh', 'std_vh', 'mean_vv',
       'median_vv', 'std_vv', 'closest_station_rain',
       'closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d', 'geometry', 'latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       '7', '8', '1', '9', '10', '11', 'Identify', 'ndvi_mean__diff',
       'ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff', 'mean_amp',
       'std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff',
       'mean_vv_diff', 'median_vv_diff', 'std_vv_diff', 'Identify2'],
      dtype='object')

In [ ]:
### get the columns fro modeling
df_model_v3=df_v3_get[['trial_id','latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       'ndvi_mean__diff','ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff',
       'mean_vh', 'median_vh', 'std_vh', 'mean_vv', 'median_vv', 'std_vv', 
       'mean_amp','std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff','mean_vv_diff', 'median_vv_diff', 'std_vv_diff',
        'closest_station_rain','closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d',
        '1', '2', '3', '4', '5', '6','Identify']]

In [ ]:
print("Successfull application",df_model_v3[df_model_v3.Identify==0].Identify.count())
print("Failure",df_model_v3[df_model_v3.Identify==1].Identify.count())
sns.countplot(data=df_model_v3, x='Identify')

## StageV4

#### Get amplitude

In [44]:
####### RESAMPLE THE IMAGE TO FINER RESOLUTION
################################################################################################################

# ### folder to store the cut images
input_path = r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\cut_tif\stage4"

#### folder to store the resample images
output_path= r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\resample_tif\stage4"

for file in os.listdir(input_path):
    
    file_path=os.path.join(input_path,file)

    src = rasterio.open(file_path)

    # Calculate the new dimensions and resolution
    new_resolution = (0.00001, -0.00001)  # New resolution in meters
    new_width = src.width * src.transform.a / new_resolution[0]
    new_height = src.height * src.transform.e / new_resolution[1]

    # Create the output TIFF file with the new dimensions and resolution
    
#     output_file = r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\cut_tif2\output.tif"

    
    prefix=file.split(".")[0]
    output_file = os.path.join(output_path, f"{prefix}_resample.tif")
    
    
    dst_transform = Affine(new_resolution[0], 0, src.transform.c, 0, new_resolution[1], src.transform.f)
    dst_profile = src.profile
    dst_profile.update(transform=dst_transform, width=int(new_width), height=int(new_height))

    # Perform the resampling
    with rasterio.open(output_file, 'w', **dst_profile) as dst:
        for i in range(1, src.count + 1):
            rasterio.warp.reproject(
                source=rasterio.band(src, i),
                destination=rasterio.band(dst, i),
                src_transform=src.transform,
                src_crs=src.crs,
                dst_transform=dst_transform,
                dst_crs=src.crs,  # Assuming the same CRS
                resampling=rasterio.enums.Resampling.bilinear
            )

In [45]:
df_v4=df_all[df_all.stage=='V4']

In [46]:
input_tif_folder= r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\resample_tif\stage4"
cnt=0

######
for index, row in df_v4.iterrows():
    cnt+=1
    print(cnt)
    id_value = row['trial_id']
    image_path_VH = os.path.join(input_tif_folder,f'{id_value}_VH_resample.tif')
    image_path_VV = os.path.join(input_tif_folder,f'{id_value}_VV_resample.tif')

    # Check if the TIF image exists
    if os.path.exists(image_path_VH) and os.path.exists(image_path_VV):
        # Extract the polygon from the 'geometry' column
        polygon = row['geometry']

        # Extract the statistics from the image within the polygon
        mean_vh, median_vh, std_vh = extract_statistics(image_path_VH, polygon)
        mean_vv, median_vv, std_vv = extract_statistics(image_path_VH, polygon)

        # Update the dataframe with the statistics
        df_v4.at[index, 'mean_vh'] = mean_vh
        df_v4.at[index, 'median_vh'] = median_vh
        df_v4.at[index, 'std_vh'] = std_vh
        df_v4.at[index, 'mean_vv'] = mean_vv
        df_v4.at[index, 'median_vv'] = median_vv
        df_v4.at[index, 'std_vv'] = std_vv
    else:
        # TIF image doesn't exist, set the values as NaN
        df_v4.at[index, 'mean_vh'] = np.nan
        df_v4.at[index, 'median_vh'] = np.nan
        df_v4.at[index, 'std_vh'] = np.nan
        df_v4.at[index, 'mean_vv'] = np.nan
        df_v4.at[index, 'median_vv'] = np.nan
        df_v4.at[index, 'std_vv'] = np.nan

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274


#### Get weather

In [51]:
# Convert the flight date column to datetime
df_v4['flight_date'] = pd.to_datetime(df_v4['flight_date']).dt.date
weather['DATE'] = pd.to_datetime(weather['DATE']).dt.date

In [52]:
cnt=0
for index, row in df_v4.iterrows():
    cnt+=1
    print(cnt)
    # Extract ID, geometry, and flight date from the current row
    ID = row['trial_id']
    geometry = row['geometry']
    flight_date = row['flight_date']
#     print(flight_date)

    # Filter the weather archive dataframe based on the flight date
    filtered_weather_df = weather[weather['DATE'] == flight_date]
    
    # Find the point closest to the centroid of the polygon
    if not filtered_weather_df.empty:
        closest_point = find_closest_point_to_centroid(geometry, filtered_weather_df)

        # Retrieve the rain and elevation values for the closest weather station
        closest_station_rain = closest_point['PRCP']
        closest_station_rain_5d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],5)
        closest_station_rain_10d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],10)
        closest_station_rain_15d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],15)

        # Add the rain and elevation values as new columns in the original dataframe
        df_v4.at[index, 'closest_station_rain'] = closest_station_rain
        df_v4.at[index, 'closest_station_rain_5d'] = closest_station_rain_5d
        df_v4.at[index, 'closest_station_rain_10d'] = closest_station_rain_10d
        df_v4.at[index, 'closest_station_rain_15d'] = closest_station_rain_15d
        
    else:
        df_v4.at[index, 'closest_station_rain'] = np.nan
        df_v4.at[index, 'closest_station_rain_5d'] = np.nan
        df_v4.at[index, 'closest_station_rain_10d'] = np.nan
        df_v4.at[index, 'closest_station_rain_15d'] = np.nan

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274


In [53]:
df_v4_get=df_v4.groupby(['trial_id','treatment']).agg({'ndvi_mean':'mean','ndvi_std':'mean','ndre_mean':'mean','ndre_std':'mean','yield':'mean',
                                             'mean_vh':'mean','median_vh':'mean', 'std_vh':'mean', 'mean_vv':'mean', 'median_vv':'mean', 'std_vv':'mean',
                                             'closest_station_rain':'mean','closest_station_rain_5d':'mean',
                                               'closest_station_rain_10d':'mean', 'closest_station_rain_15d':'mean',
                                                       'geometry': unary_union})
df_v4_get=df_v4_get.reset_index()

#### Add latitude and longitude as features

In [55]:
get_centroid=df_v4_get[['geometry']]
gdf = gpd.GeoDataFrame(get_centroid, geometry='geometry')
# Compute the centroid of each polygon
gdf['centroid'] = gdf['geometry'].centroid

# Extract latitude and longitude from the centroid
df_v4_get['latitude']=gdf.centroid.y
df_v4_get['longitude'] = gdf.centroid.x

df_v4_get['longitude']=df_v4_get['longitude']+360

#### NDRE and NDVI

In [56]:
df_v4_get['norm_ndvi_mean'] = scaler.fit_transform(df_v4_get[['ndvi_mean']])
df_v4_get['norm_ndvi_std'] = scaler.fit_transform(df_v4_get[['ndvi_std']].values)
df_v4_get['norm_ndre_mean'] = scaler.fit_transform(df_v4_get[['ndre_mean']].values)
df_v4_get['norm_ndre_std'] = scaler.fit_transform(df_v4_get[['ndre_std']].values)

#### treatment

In [57]:
treat_encoder = OneHotEncoder(handle_unknown='ignore')
treat_onehot=treat_encoder.fit_transform(df_v4_get[['treatment']])
treatments=pd.DataFrame(treat_onehot.toarray())

all_treatments=treat_encoder.categories_[0]
for i in range(len(all_treatments)):
    df_v4_get[str(all_treatments[i])]=treatments.iloc[:,i]

### Judge product failure based on yield data
trials=df_v4_get['trial_id'].tolist()
yields=df_v4_get['yield'].tolist()

Identifys=[]

for i in range(len(trials)):
    trail_id=trials[i]
    yie=float(yields[i])
    
    select=df_v4_get[(df_v4_get['trial_id'] == trail_id) & (df_v4_get['treatment']==3)]
    
#     print(trail_id)
    reference = select['yield'].values[0]
    
    check = 1 if abs(yie-reference) > reference*0.03 else 0
    Identifys.append(check)
    
df_v4_get['Identify'] = Identifys

#### Get more features - compare with treatment 1 condition

In [58]:
df_v4_get['ndvi_mean__diff'] = df_v4_get.groupby('trial_id')['norm_ndvi_mean'].transform(lambda x: x - x.iloc[0])
df_v4_get['ndvi_std_diff'] = df_v4_get.groupby('trial_id')['norm_ndvi_std'].transform(lambda x: x - x.iloc[0])
df_v4_get['ndre_mean_diff'] = df_v4_get.groupby('trial_id')['norm_ndre_mean'].transform(lambda x: x - x.iloc[0])
df_v4_get['ndre_std_diff'] = df_v4_get.groupby('trial_id')['norm_ndre_std'].transform(lambda x: x - x.iloc[0])

In [59]:
df_v4_get['mean_amp']=(df_v4_get['mean_vh']+df_v4_get['mean_vv'])/2
df_v4_get['std_amp']=(df_v4_get['std_vh']+df_v4_get['std_vv'])/2

df_v4_get['mean_vh_diff'] = df_v4_get.groupby('trial_id')['mean_vh'].transform(lambda x: x - x.iloc[0])
df_v4_get['median_vh_diff'] = df_v4_get.groupby('trial_id')['median_vh'].transform(lambda x: x - x.iloc[0])
df_v4_get['std_vh_diff'] = df_v4_get.groupby('trial_id')['std_vh'].transform(lambda x: x - x.iloc[0])
df_v4_get['mean_vv_diff'] = df_v4_get.groupby('trial_id')['mean_vv'].transform(lambda x: x - x.iloc[0])
df_v4_get['median_vv_diff'] = df_v4_get.groupby('trial_id')['median_vv'].transform(lambda x: x - x.iloc[0])
df_v4_get['std_vv_diff'] = df_v4_get.groupby('trial_id')['std_vv'].transform(lambda x: x - x.iloc[0])

In [76]:
df_v4_get.columns=['trial_id', 'treatment', 'ndvi_mean', 'ndvi_std', 'ndre_mean',
       'ndre_std', 'yield', 'mean_vh', 'median_vh', 'std_vh', 'mean_vv',
       'median_vv', 'std_vv', 'closest_station_rain',
       'closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d', 'geometry', 'latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       '7','8','1','9','10','11','Identify', 'ndvi_mean__diff',
       'ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff', 'mean_amp',
       'std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff',
       'mean_vv_diff', 'median_vv_diff', 'std_vv_diff']

In [17]:
### save all data in case
df_v4_get.to_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\df_v4_get_incase_502.csv',index=None)

In [16]:
df_v4_get=pd.read_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\df_v4_get_incase_502.csv')

trials=df_v4_get['trial_id'].tolist()
yields=df_v4_get['yield'].tolist()

Identifys2=[]

for i in range(len(trials)):
    trail_id=trials[i]
    yie=float(yields[i])
    
    select=df_v4_get[(df_v4_get['trial_id'] == trail_id) & (df_v4_get['treatment']==3)]
    
#     print(trail_id)
    reference = select['yield'].values[0]
    
    check = 1 if yie - reference < (reference * -0.03) else 0
    Identifys2.append(check)

df_v4_get['Identify2'] = Identifys2

In [ ]:
### get the columns fro modeling
df_model_v4=df_v4_get[['trial_id','latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       'ndvi_mean__diff','ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff',
       'mean_vh', 'median_vh', 'std_vh', 'mean_vv', 'median_vv', 'std_vv', 
       'mean_amp','std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff','mean_vv_diff', 'median_vv_diff', 'std_vv_diff',
        'closest_station_rain','closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d',
        '1', '2', '3', '4', '5', '6','Identify']]

In [ ]:
print("Successfull application",df_model_v4[df_model_v4.Identify==0].Identify.count())
print("Failure",df_model_v4[df_model_v4.Identify==1].Identify.count())
sns.countplot(data=df_model_v4, x='Identify')

## StageV6

#### Get amplitude

In [61]:
####### RESAMPLE THE IMAGE TO FINER RESOLUTION
################################################################################################################

# ### folder to store the cut images
input_path = r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\cut_tif\stage6"

#### folder to store the resample images
output_path= r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\resample_tif\stage6"

for file in os.listdir(input_path):
    
    file_path=os.path.join(input_path,file)

    src = rasterio.open(file_path)

    # Calculate the new dimensions and resolution
    new_resolution = (0.00001, -0.00001)  # New resolution in meters
    new_width = src.width * src.transform.a / new_resolution[0]
    new_height = src.height * src.transform.e / new_resolution[1]
    
    
    prefix=file.split(".")[0]
    output_file = os.path.join(output_path, f"{prefix}_resample.tif")
    
    
    dst_transform = Affine(new_resolution[0], 0, src.transform.c, 0, new_resolution[1], src.transform.f)
    dst_profile = src.profile
    dst_profile.update(transform=dst_transform, width=int(new_width), height=int(new_height))

    # Perform the resampling
    with rasterio.open(output_file, 'w', **dst_profile) as dst:
        for i in range(1, src.count + 1):
            rasterio.warp.reproject(
                source=rasterio.band(src, i),
                destination=rasterio.band(dst, i),
                src_transform=src.transform,
                src_crs=src.crs,
                dst_transform=dst_transform,
                dst_crs=src.crs,  # Assuming the same CRS
                resampling=rasterio.enums.Resampling.bilinear
            )

In [62]:
df_v6=df_all[df_all.stage=='V6']

In [63]:
input_tif_folder= r"C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\resample_tif\stage6"
cnt=0

######
for index, row in df_v6.iterrows():
    cnt+=1
    print(cnt)
    id_value = row['trial_id']
    image_path_VH = os.path.join(input_tif_folder,f'{id_value}_VH_resample.tif')
    image_path_VV = os.path.join(input_tif_folder,f'{id_value}_VV_resample.tif')

    # Check if the TIF image exists
    if os.path.exists(image_path_VH) and os.path.exists(image_path_VV):
        # Extract the polygon from the 'geometry' column
        polygon = row['geometry']

        # Extract the statistics from the image within the polygon
        mean_vh, median_vh, std_vh = extract_statistics(image_path_VH, polygon)
        mean_vv, median_vv, std_vv = extract_statistics(image_path_VH, polygon)

        # Update the dataframe with the statistics
        df_v6.at[index, 'mean_vh'] = mean_vh
        df_v6.at[index, 'median_vh'] = median_vh
        df_v6.at[index, 'std_vh'] = std_vh
        df_v6.at[index, 'mean_vv'] = mean_vv
        df_v6.at[index, 'median_vv'] = median_vv
        df_v6.at[index, 'std_vv'] = std_vv
    else:
        # TIF image doesn't exist, set the values as NaN
        df_v6.at[index, 'mean_vh'] = np.nan
        df_v6.at[index, 'median_vh'] = np.nan
        df_v6.at[index, 'std_vh'] = np.nan
        df_v6.at[index, 'mean_vv'] = np.nan
        df_v6.at[index, 'median_vv'] = np.nan
        df_v6.at[index, 'std_vv'] = np.nan

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274


#### Get weather

In [65]:
# Convert the flight date column to datetime
df_v6['flight_date'] = pd.to_datetime(df_v6['flight_date']).dt.date
weather['DATE'] = pd.to_datetime(weather['DATE']).dt.date

In [66]:
cnt=0

for index, row in df_v6.iterrows():
    cnt+=1
    print(cnt)
    # Extract ID, geometry, and flight date from the current row
    ID = row['trial_id']
    geometry = row['geometry']
    flight_date = row['flight_date']
#     print(flight_date)

    # Filter the weather archive dataframe based on the flight date
    filtered_weather_df = weather[weather['DATE'] == flight_date]
    
    # Find the point closest to the centroid of the polygon
    if not filtered_weather_df.empty:
        closest_point = find_closest_point_to_centroid(geometry, filtered_weather_df)

        # Retrieve the rain and elevation values for the closest weather station
        closest_station_rain = closest_point['PRCP']
        closest_station_rain_5d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],5)
        closest_station_rain_10d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],10)
        closest_station_rain_15d = cal_rolling_sums(closest_point['STATION'],closest_point['DATE'],15)

        # Add the rain and elevation values as new columns in the original dataframe
        df_v6.at[index, 'closest_station_rain'] = closest_station_rain
        df_v6.at[index, 'closest_station_rain_5d'] = closest_station_rain_5d
        df_v6.at[index, 'closest_station_rain_10d'] = closest_station_rain_10d
        df_v6.at[index, 'closest_station_rain_15d'] = closest_station_rain_15d
    
    else:
#         print(index,ID,flight_date)
        df_v6.at[index, 'closest_station_rain'] = np.nan
        df_v6.at[index, 'closest_station_rain_5d'] = np.nan
        df_v6.at[index, 'closest_station_rain_10d'] = np.nan
        df_v6.at[index, 'closest_station_rain_15d'] = np.nan

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274


In [78]:
df_v6_get=df_v6.groupby(['trial_id','treatment']).agg({'ndvi_mean':'mean','ndvi_std':'mean','ndre_mean':'mean','ndre_std':'mean','yield':'mean',
                                             'mean_vh':'mean','median_vh':'mean', 'std_vh':'mean', 'mean_vv':'mean', 'median_vv':'mean', 'std_vv':'mean',
                                             'closest_station_rain':'mean','closest_station_rain_5d':'mean','closest_station_rain_10d':'mean',
                                            'closest_station_rain_15d':'mean','geometry': unary_union})
df_v6_get=df_v6_get.reset_index()

#### Add latitude and longitude as features

In [80]:
get_centroid=df_v6_get[['geometry']]
gdf = gpd.GeoDataFrame(get_centroid, geometry='geometry')
# Compute the centroid of each polygon
gdf['centroid'] = gdf['geometry'].centroid

# Extract latitude and longitude from the centroid
df_v6_get['latitude']=gdf.centroid.y
df_v6_get['longitude'] = gdf.centroid.x

df_v6_get['longitude']=df_v6_get['longitude']+360

#### NDRE and NDVI

In [81]:
df_v6_get['norm_ndvi_mean'] = scaler.fit_transform(df_v6_get[['ndvi_mean']])
df_v6_get['norm_ndvi_std'] = scaler.fit_transform(df_v6_get[['ndvi_std']].values)
df_v6_get['norm_ndre_mean'] = scaler.fit_transform(df_v6_get[['ndre_mean']].values)
df_v6_get['norm_ndre_std'] = scaler.fit_transform(df_v6_get[['ndre_std']].values)

#### treatment

In [82]:
treat_encoder = OneHotEncoder(handle_unknown='ignore')
treat_onehot=treat_encoder.fit_transform(df_v6_get[['treatment']])
treatments=pd.DataFrame(treat_onehot.toarray())

all_treatments=treat_encoder.categories_[0]
for i in range(len(all_treatments)):
    df_v6_get[str(all_treatments[i])]=treatments.iloc[:,i]

### Judge product failure based on yield data
trials=df_v6_get['trial_id'].tolist()
yields=df_v6_get['yield'].tolist()

Identifys=[]

for i in range(len(trials)):
    trail_id=trials[i]
    yie=float(yields[i])
    
    select=df_v6_get[(df_v6_get['trial_id'] == trail_id) & (df_v6_get['treatment']==3)]
    
#     print(trail_id)
    reference = select['yield'].values[0]
    
    check = 1 if abs(yie-reference) > reference*0.03 else 0
    Identifys.append(check)
    
df_v6_get['Identify'] = Identifys

#### Get more features - compare with treatment 1 condition

In [83]:
df_v6_get['ndvi_mean__diff'] = df_v6_get.groupby('trial_id')['norm_ndvi_mean'].transform(lambda x: x - x.iloc[0])
df_v6_get['ndvi_std_diff'] = df_v6_get.groupby('trial_id')['norm_ndvi_std'].transform(lambda x: x - x.iloc[0])
df_v6_get['ndre_mean_diff'] = df_v6_get.groupby('trial_id')['norm_ndre_mean'].transform(lambda x: x - x.iloc[0])
df_v6_get['ndre_std_diff'] = df_v6_get.groupby('trial_id')['norm_ndre_std'].transform(lambda x: x - x.iloc[0])

In [84]:
df_v6_get['mean_amp']=(df_v6_get['mean_vh']+df_v6_get['mean_vv'])/2
df_v6_get['std_amp']=(df_v6_get['std_vh']+df_v6_get['std_vv'])/2

df_v6_get['mean_vh_diff'] = df_v6_get.groupby('trial_id')['mean_vh'].transform(lambda x: x - x.iloc[0])
df_v6_get['median_vh_diff'] = df_v6_get.groupby('trial_id')['median_vh'].transform(lambda x: x - x.iloc[0])
df_v6_get['std_vh_diff'] = df_v6_get.groupby('trial_id')['std_vh'].transform(lambda x: x - x.iloc[0])
df_v6_get['mean_vv_diff'] = df_v6_get.groupby('trial_id')['mean_vv'].transform(lambda x: x - x.iloc[0])
df_v6_get['median_vv_diff'] = df_v6_get.groupby('trial_id')['median_vv'].transform(lambda x: x - x.iloc[0])
df_v6_get['std_vv_diff'] = df_v6_get.groupby('trial_id')['std_vv'].transform(lambda x: x - x.iloc[0])

In [85]:
df_v6_get.columns=['trial_id', 'treatment', 'ndvi_mean', 'ndvi_std', 'ndre_mean',
       'ndre_std', 'yield', 'mean_vh', 'median_vh', 'std_vh', 'mean_vv',
       'median_vv', 'std_vv', 'closest_station_rain',
       'closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d', 'geometry', 'latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       '7','8','1','9','10','11','Identify', 'ndvi_mean__diff',
       'ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff', 'mean_amp',
       'std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff',
       'mean_vv_diff', 'median_vv_diff', 'std_vv_diff']

In [19]:
### save all data in case
df_v6_get.to_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\df_v6_get_incase_502.csv',index=None)

In [18]:
df_v6_get=pd.read_csv(r'C:\Users\XiaoYu\OneDrive - Pivot Bio\Desktop\work\Protocol_502\df_v6_get_incase_502.csv')

trials=df_v6_get['trial_id'].tolist()
yields=df_v6_get['yield'].tolist()

Identifys2=[]

for i in range(len(trials)):
    trail_id=trials[i]
    yie=float(yields[i])
    
    select=df_v6_get[(df_v6_get['trial_id'] == trail_id) & (df_v6_get['treatment']==3)]
    
#     print(trail_id)
    reference = select['yield'].values[0]
    
    check = 1 if yie - reference < (reference * -0.03) else 0
    Identifys2.append(check)

df_v6_get['Identify2'] = Identifys2

In [20]:
df_v6_get.columns

Index(['trial_id', 'treatment', 'ndvi_mean', 'ndvi_std', 'ndre_mean',
       'ndre_std', 'yield', 'mean_vh', 'median_vh', 'std_vh', 'mean_vv',
       'median_vv', 'std_vv', 'closest_station_rain',
       'closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d', 'geometry', 'latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       '7', '8', '1', '9', '10', '11', 'Identify', 'ndvi_mean__diff',
       'ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff', 'mean_amp',
       'std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff',
       'mean_vv_diff', 'median_vv_diff', 'std_vv_diff', 'Identify2'],
      dtype='object')

In [ ]:
### get the columns fro modeling
df_model_v6=df_v6_get[['trial_id','latitude', 'longitude',
       'norm_ndvi_mean', 'norm_ndvi_std', 'norm_ndre_mean', 'norm_ndre_std',
       'ndvi_mean__diff','ndvi_std_diff', 'ndre_mean_diff', 'ndre_std_diff',
       'mean_vh', 'median_vh', 'std_vh', 'mean_vv', 'median_vv', 'std_vv', 
       'mean_amp','std_amp', 'mean_vh_diff', 'median_vh_diff', 'std_vh_diff','mean_vv_diff', 'median_vv_diff', 'std_vv_diff',
        'closest_station_rain','closest_station_rain_5d', 'closest_station_rain_10d',
       'closest_station_rain_15d',
        '1', '2', '3', '4', '5', '6','Identify']]

In [ ]:
print("Successfull application",df_model_v6[df_model_v6.Identify==0].Identify.count())
print("Failure",df_model_v6[df_model_v6.Identify==1].Identify.count())
sns.countplot(data=df_model_v6, x='Identify')